<a href="https://colab.research.google.com/github/MKrezheska/data-mining-project/blob/main/1_DataGathering.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Проект по предметот податочно рударство


1. **Градење на податочното множество**. Дел од податоците ги собереме со Spotify Web API (spotipy), a дел со скрапирање на веб страната *organizeyourmusic.playlistmachinery.com/*.



*   Вчитување на потребните библиотеки и веб драјверот.



In [ ]:
!pip install selenium
!apt-get update 
!apt install chromium-chromedriver

from selenium import webdriver
chrome_options = webdriver.ChromeOptions()
chrome_options.add_argument('--headless')
chrome_options.add_argument('--no-sandbox')
chrome_options.add_argument('--disable-dev-shm-usage')
wd = webdriver.Chrome('chromedriver',chrome_options=chrome_options)
driver =webdriver.Chrome('chromedriver',chrome_options=chrome_options)

In [ ]:
driver.get("http://organizeyourmusic.playlistmachinery.com/")
button = driver.find_element_by_id('go')
button.click()



*   Најава на веб страната *organizeyourmusic.playlistmachinery.com/*.



In [ ]:
username = driver.find_element_by_id("login-username")
username.clear()
username.send_keys("podatocno@gmail.com")

password = driver.find_element_by_id("login-password")
password.clear()
password.send_keys("prproekt123.")

driver.find_element_by_id("login-button").click()



*   Преземање на playlist-тата со песните кои ќе бидат означени како „добри песни“.



In [ ]:
driver.get("http://organizeyourmusic.playlistmachinery.com/")
from selenium.webdriver.support.ui import Select

select = Select(driver.find_element_by_id('collection-type'))

select.select_by_value('playlist')

In [ ]:
pid_g = driver.find_element_by_id("uri-text")
pid_g.clear()
pid_g.send_keys("spotify:playlist:0MSvVCtdco07nI3ZWQsl9Y")

button = driver.find_element_by_id('go')
button.click()

In [ ]:
for _ in range(1000):
  try:
    driver.find_element_by_id("Sources").click()
    break
  except:
    continue

good_fileContent = driver.page_source.encode('utf-8')




*   Парсирање на табелата со песни и извлекување на потребните информации за нив.



In [ ]:
import requests
import lxml.html as lh
import pandas as pd


doc = lh.fromstring(good_fileContent)
tr_elements = doc.xpath('//tr')

col=[]
i=0
for t in tr_elements[0]:
    i+=1
    name=t.text_content()
    col.append((name,[]))

for j in range(1,len(tr_elements)):
    T=tr_elements[j]
    
    i=0
    
    for t in T.iterchildren():
        data=t.text_content() 
        
        col[i][1].append(data)
        i+=1

Dict={title:column for (title,column) in col}
df_genres_good=pd.DataFrame(Dict)



*   Приказ на собраните податоци.



In [ ]:
pd.set_option('display.max_rows',None)
df_genres_good=df_genres_good.drop([df_genres_good.columns[0],df_genres_good.columns[1],df_genres_good.columns[2]],axis=1)
df_genres_good.head(3000)

title  ... pop
0                                       Blinding Lights  ...  96
1                                               bad guy  ...  88
2                                  lovely (with Khalid)  ...  88
3                                   everything i wanted  ...  87
4                                              Believer  ...  87
5                                          In Your Eyes  ...  87
6                                             my future  ...  86
7                                 when the party's over  ...  85
8                           Godzilla (feat. Juice WRLD)  ...  85
9                                               Thunder  ...  84
10                                           In the End  ...  83
11                                     Do I Wanna Know?  ...  83
12                                              Starboy  ...  83
13                                           i love you  ...  82
14                                           ocean eyes  ...  82
15                                     Call Out My Name  ...  82
16                                       No Time To Die  ...  81
17                               idontwannabeyouanymore  ...  81
18                                              Natural  ...  81
19                                             Bad Liar  ...  81
20                         you should see me in a crown  ...  80
21                                        bury a friend  ...  80
22                                               Demons  ...  80
23                                    Whatever It Takes  ...  80
24                                         Viva La Vida  ...  80
25                                            Heartless  ...  80
26                                          After Hours  ...  80
27                        all the good girls go to hell  ...  79
28                                    wish you were gay  ...  79
29                                     I Feel It Coming  ...  79
30                                   listen before i go  ...  78
31                                            R U Mine?  ...  78
32             Why'd You Only Call Me When You're High?  ...  78
33                                 Hymn for the Weekend  ...  78
34                                      Save Your Tears  ...  78
35                                                xanny  ...  77
36                                       What I've Done  ...  77
37                       Lucky You (feat. Joyner Lucas)  ...  77
38                                             Paranoid  ...  77
39                                                  505  ...  77
40                                          Radioactive  ...  77
41                        Sugar (feat. Francesco Yates)  ...  77
42                                  A Sky Full of Stars  ...  77
43                                          Die For You  ...  77
44                                 my strange addiction  ...  76
45                                              ilomilo  ...  76
46                                              COPYCAT  ...  76
47                                            bellyache  ...  76
48                                       Six Feet Under  ...  76
49                                      One Step Closer  ...  76
50                               Fluorescent Adolescent  ...  76
51                                bitches broken hearts  ...  75
52                                               my boy  ...  75
53                                              hostage  ...  75
54                              Adventure of a Lifetime  ...  75
55                                   When We Were Young  ...  75
56                                                    8  ...  74
57                                                Bored  ...  74
58                                             Crawling  ...  74
59                Venom - Music From The Motion Picture  ...  74
60                                           Doin' Time  ...  74
61                  

* Селекција на подмножество на атрибутите и додавање на 'target' атрибут кој покажува дали песната е „добра“ или не.

In [ ]:
df_genres_good = df_genres_good.filter(['title','top genre','year'])
df_genres_good['target'] = [1 for _ in range(len(df_genres_good.index))]

In [ ]:
df_genres_good.head(2000)

title  ... target
0                                       Blinding Lights  ...      1
1                                             my future  ...      1
2                                               bad guy  ...      1
3                                          In Your Eyes  ...      1
4                                   everything i wanted  ...      1
5                                  lovely (with Khalid)  ...      1
6                           Godzilla (feat. Juice WRLD)  ...      1
7                                              Believer  ...      1
8                                 when the party's over  ...      1
9                                               Thunder  ...      1
10                                           In the End  ...      1
11                                              Starboy  ...      1
12                                           i love you  ...      1
13                                           ocean eyes  ...      1
14                                     Do I Wanna Know?  ...      1
15                               idontwannabeyouanymore  ...      1
16                                              Natural  ...      1
17                                             Bad Liar  ...      1
18                                            Heartless  ...      1
19                                     Call Out My Name  ...      1
20                         you should see me in a crown  ...      1
21                                    wish you were gay  ...      1
22                                        bury a friend  ...      1
23                                       No Time To Die  ...      1
24                                    Whatever It Takes  ...      1
25                                          After Hours  ...      1
26                        all the good girls go to hell  ...      1
27                                               Demons  ...      1
28                                         Viva La Vida  ...      1
29                                     I Feel It Coming  ...      1
30                                   listen before i go  ...      1
31                                                xanny  ...      1
32                                 my strange addiction  ...      1
33                                              ilomilo  ...      1
34                                            R U Mine?  ...      1
35                        Sugar (feat. Francesco Yates)  ...      1
36                                  A Sky Full of Stars  ...      1
37                                 Hymn for the Weekend  ...      1
38                                      Save Your Tears  ...      1
39                                              COPYCAT  ...      1
40                                            bellyache  ...      1
41                                       Six Feet Under  ...      1
42                                       What I've Done  ...      1
43                       Lucky You (feat. Joyner Lucas)  ...      1
44                                             Paranoid  ...      1
45             Why'd You Only Call Me When You're High?  ...      1
46                                                  505  ...      1
47                                          Radioactive  ...      1
48                                          Die For You  ...      1
49                                bitches broken hearts  ...      1
50                                               my boy  ...      1
51                                              hostage  ...      1
52                                                Bored  ...      1
53                                      One Step Closer  ...      1
54                               Fluorescent Adolescent  ...      1
55                                                    8  ...      1
56                                             Crawling  ...      1
57                                           Doin' Time  ...      1
58                 Smoke On The Water 



*   Истото го повторуваме и за песните кои се од playlist-тата која ги содржи „лошите“ песни.



In [ ]:
driver.get("http://organizeyourmusic.playlistmachinery.com/")
select = Select(driver.find_element_by_id('collection-type'))

select.select_by_value('playlist')

In [ ]:
pid_b = driver.find_element_by_id("uri-text")
pid_b.clear()
pid_b.send_keys("spotify:playlist:4TMShuRj0r3ePfupxOa058")

button = driver.find_element_by_id('go')
button.click()

In [ ]:
for _ in range(1000):
  try:
    driver.find_element_by_id("Sources").click()
    break
  except:
    continue

bad_fileContent = driver.page_source.encode('utf-8')

In [ ]:
doc = lh.fromstring(bad_fileContent)
tr_elements = doc.xpath('//tr')

col=[]
i=0
for t in tr_elements[0]:
    i+=1
    name=t.text_content()
    col.append((name,[]))

for j in range(1,len(tr_elements) ):
    T=tr_elements[j]
    
    i=0
    
    for t in T.iterchildren():
        data=t.text_content() 
        
        col[i][1].append(data)
        i+=1

Dict={title:column for (title,column) in col}
df_genres_bad=pd.DataFrame(Dict)

In [ ]:
df_genres_bad = df_genres_bad.filter(['title','top genre','year'])
df_genres_bad['target'] = [0 for _ in range(len(df_genres_bad.index))]
df_genres_bad.head(2000)

title  ... target
0                      WAP (feat. Megan Thee Stallion)  ...      0
1                                       Break My Heart  ...      0
2                                      Don't Start Now  ...      0
3                             Intentions (feat. Quavo)  ...      0
4                                               Savage  ...      0
5                                            I Like It  ...      0
6                                          Hallucinate  ...      0
7                             One Kiss (with Dua Lipa)  ...      0
8                                             Physical  ...      0
9     I Think I'm OKAY (with YUNGBLUD & Travis Barker)  ...      0
10                                        Captain Hook  ...      0
11                                 Scared to Be Lonely  ...      0
12                                                FEFE  ...      0
13                          Candy (feat. Trippie Redd)  ...      0
14                                       We Can't Stop  ...      0
15                              Oops!...I Did It Again  ...      0
16                                               Yummy  ...      0
17                                        Bodak Yellow  ...      0
18                            Cash Shit (feat. DaBaby)  ...      0
19                               ...Baby One More Time  ...      0
20                                              Malibu  ...      0
21                                          Levitating  ...      0
22                                    Kiss and Make Up  ...      0
23                                              No Lie  ...      0
24                                                Baby  ...      0
25                Forever (feat. Post Malone & Clever)  ...      0
26                                       Wrecking Ball  ...      0
27                         Electricity (with Dua Lipa)  ...      0
28                                       Play It Again  ...      0
29                                            Betrayed  ...      0
30                               Him & I (with Halsey)  ...      0
31                                            No Limit  ...      0
32                                                Cool  ...      0
33                                       Pretty Please  ...      0
34                                     Thru Your Phone  ...      0
35                                          Love Again  ...      0
36                                            Sex Talk  ...      0
37             Nobody But You (Duet with Gwen Stefani)  ...      0
38                                                Roar  ...      0
39                                          Super Bass  ...      0
40                      Glass House (feat. Naomi Wild)  ...      0
41                                        Eenie Meenie  ...      0
42                                      Come Around Me  ...      0
43                                          Be Careful  ...      0
44                                  Cry About It Later  ...      0
45                                    Future Nostalgia  ...      0
46                                         Good In Bed  ...      0
47                     Bartier Cardi (feat. 21 Savage)  ...      0
48                                    I Do (feat. SZA)  ...      0
49                             That's My Kind Of Night  ...      0
50                                             Daisies  ...      0
51                                          Gucci Gang  ...      0
52                                           el Diablo  ...      0
53                                           Adore You  ...      0
54                                   Boys Will Be Boys  ...      0
55                        What If I Never Get Over You  ...      0
56                                            Habitual  ...      0
57                                Ring (feat. Kehlani)  ...      0
58                                   Never Really Over  ...      0
59                           

* Спојување во двете множества во едно.

In [ ]:
df_genres = df_genres_good.append(df_genres_bad, ignore_index=True)

In [ ]:
df_genres.head(2000)

title  ... target
0                                       Blinding Lights  ...      1
1                                             my future  ...      1
2                                               bad guy  ...      1
3                                          In Your Eyes  ...      1
4                                   everything i wanted  ...      1
5                                  lovely (with Khalid)  ...      1
6                           Godzilla (feat. Juice WRLD)  ...      1
7                                              Believer  ...      1
8                                 when the party's over  ...      1
9                                               Thunder  ...      1
10                                           In the End  ...      1
11                                              Starboy  ...      1
12                                           i love you  ...      1
13                                           ocean eyes  ...      1
14                                     Do I Wanna Know?  ...      1
15                               idontwannabeyouanymore  ...      1
16                                              Natural  ...      1
17                                             Bad Liar  ...      1
18                                            Heartless  ...      1
19                                     Call Out My Name  ...      1
20                         you should see me in a crown  ...      1
21                                    wish you were gay  ...      1
22                                        bury a friend  ...      1
23                                       No Time To Die  ...      1
24                                    Whatever It Takes  ...      1
25                                          After Hours  ...      1
26                        all the good girls go to hell  ...      1
27                                               Demons  ...      1
28                                         Viva La Vida  ...      1
29                                     I Feel It Coming  ...      1
30                                   listen before i go  ...      1
31                                                xanny  ...      1
32                                 my strange addiction  ...      1
33                                              ilomilo  ...      1
34                                            R U Mine?  ...      1
35                        Sugar (feat. Francesco Yates)  ...      1
36                                  A Sky Full of Stars  ...      1
37                                 Hymn for the Weekend  ...      1
38                                      Save Your Tears  ...      1
39                                              COPYCAT  ...      1
40                                            bellyache  ...      1
41                                       Six Feet Under  ...      1
42                                       What I've Done  ...      1
43                       Lucky You (feat. Joyner Lucas)  ...      1
44                                             Paranoid  ...      1
45             Why'd You Only Call Me When You're High?  ...      1
46                                                  505  ...      1
47                                          Radioactive  ...      1
48                                          Die For You  ...      1
49                                bitches broken hearts  ...      1
50                                               my boy  ...      1
51                                              hostage  ...      1
52                                                Bored  ...      1
53                                      One Step Closer  ...      1
54                               Fluorescent Adolescent  ...      1
55                                                    8  ...      1
56                                             Crawling  ...      1
57                                           Doin' Time  ...      1
58                 Smoke On The Water 

* Другите податоци за песните ги земаме со помош на Spotify Web API (spotipy).

In [ ]:
!pip install spotipy
!pip install sklearn

* Податоци потребни за поврзување со соодветниот Spotify account каде се наоѓаат playlist-ите и беше направен исклучиво за потребите на овој проект.

In [ ]:
client_id = "158af8a526e940cd82a1ebf4bbceaec9"
client_secret = "6fa7e66a1b6c4fa490a425a9e1a2a25e"

In [ ]:
%env SPOTIPY_CLIENT_ID=$client_id
%env SPOTIPY_CLIENT_SECRET=$client_secret 

env: SPOTIPY_CLIENT_ID=158af8a526e940cd82a1ebf4bbceaec9
env: SPOTIPY_CLIENT_SECRET=6fa7e66a1b6c4fa490a425a9e1a2a25e


In [ ]:
username="7m07drxdmjlwhmdhd17heiwb2"
good_playlist="0MSvVCtdco07nI3ZWQsl9Y"
bad_playlist="4TMShuRj0r3ePfupxOa058"

* Импортирање на соодветните библиотеки.

In [ ]:
import argparse
import pprint
import sys
import os
import subprocess
import json
import spotipy
import spotipy.util as util
import pandas as pd

from spotipy.oauth2 import SpotifyClientCredentials

client_credentials_manager = SpotifyClientCredentials()

* Функции за соодветно земање на деталите потребни за секоја песна кои го користат api-то.

In [ ]:
def get_playlist_content(username, playlist_id, sp):
    offset = 0
    songs = []
    while True:
        content = sp.user_playlist_tracks(username, playlist_id, fields=None,
                                          limit=100, offset=offset, market=None)
        songs += content['items']
        if content['next'] is not None:
            offset += 100
        else:
            break

    with open('{}-{}'.format(username, playlist_id), 'w') as outfile:
        json.dump(songs, outfile)


def get_playlist_audio_features(username, playlist_id, sp):
    offset = 0
    songs = []
    items = []
    ids = []
    while True:
        content = sp.user_playlist_tracks(username, playlist_id, fields=None, limit=100, offset=offset, market=None)
        songs += content['items']
        if content['next'] is not None:
            offset += 100
        else:
            break

    for i in songs:
        ids.append(i['track']['id'])

    index = 0
    audio_features = []
    while index < len(ids):
        audio_features += sp.audio_features(ids[index:index + 50])
        index += 50

    features_list = []
    for features in audio_features:

        lz_uri = features['uri']
        results = sp.track(lz_uri)
        title = results['name']
        popularity = results['popularity']

        artist = results['artists'][0]['name'];
        if(len(results['artists']) > 1):
          for i in range(1, len(results['artists']) - 1):
            artist = artist + ' & ' +results['artists'][i]['name']
          
          artist = artist + ' & ' + results['artists'][-1]['name']

        features_list.append([features['energy'], features['liveness'],
                              features['tempo'], features['speechiness'],
                              features['acousticness'], features['instrumentalness'],
                              features['time_signature'], features['danceability'],
                              features['key'], features['duration_ms'],
                              features['loudness'], features['valence'],
                              features['mode'], features['type'], popularity,
                              features['uri'], title, artist])
        

    df = pd.DataFrame(features_list, columns=['energy', 'liveness',
                                              'tempo', 'speechiness',
                                              'acousticness', 'instrumentalness',
                                              'time_signature', 'danceability',
                                              'key', 'duration_ms', 'loudness',
                                              'valence', 'mode', 'type', 'popularity','uri', 'title', 'artist'])
    df.to_csv('{}-{}.csv'.format(username, playlist_id), index=False)


def get_user_playlist(username, sp):
    playlists = sp.user_playlists(username)
    for playlist in playlists['items']:
        print("Name: {}, Number of songs: {}, Playlist ID: {} ".
              format(playlist['name'].encode('utf8'),
                     playlist['tracks']['total'],
                     playlist['id']))

In [ ]:
def getData(username, playlist):
    sp = spotipy.Spotify(client_credentials_manager=client_credentials_manager)
    print("Getting user playlist")
    get_user_playlist(username, sp)
    print("Getting playlist content")
    get_playlist_content(username, playlist, sp)
    print("Getting playlist audio features")
    get_playlist_audio_features(username, playlist, sp)

* Вчитување на податоците за песните од playlist-тата кои се означени како како „добри песни“.

In [ ]:
getData(username, good_playlist)

Getting user playlist
Name: b'GOOD', Number of songs: 1004, Playlist ID: 0MSvVCtdco07nI3ZWQsl9Y 
Name: b'BAD', Number of songs: 987, Playlist ID: 4TMShuRj0r3ePfupxOa058 
Name: b'Test', Number of songs: 2939, Playlist ID: 7kxFRqwR0wEkkaXffQc5Gw 
Getting playlist content
Getting playlist audio features


In [ ]:
df_good_spotipy = pd.read_csv("7m07drxdmjlwhmdhd17heiwb2-0MSvVCtdco07nI3ZWQsl9Y.csv")

In [ ]:
df_good_spotipy.head(3000)

energy  ...                                             artist
0     0.4250  ...                                      Billie Eilish
1     0.1250  ...                                      Billie Eilish
2     0.5330  ...                                      Billie Eilish
3     0.4440  ...                                      Billie Eilish
4     0.3510  ...                                      Billie Eilish
5     0.1110  ...                                      Billie Eilish
6     0.2350  ...                                      Billie Eilish
7     0.3050  ...                                      Billie Eilish
8     0.3890  ...                                      Billie Eilish
9     0.4230  ...                                      Billie Eilish
10    0.0561  ...                                      Billie Eilish
11    0.1310  ...                                      Billie Eilish
12    0.1380  ...                                      Billie Eilish
13    0.3090  ...                                      Billie Eilish
14    0.2190  ...                                      Billie Eilish
15    0.2250  ...                                      Billie Eilish
16    0.3320  ...                                      Billie Eilish
17    0.3210  ...                                      Billie Eilish
18    0.2960  ...                             Billie Eilish & Khalid
19    0.4220  ...                                      Billie Eilish
20    0.3880  ...                                      Billie Eilish
21    0.4120  ...                                      Billie Eilish
22    0.3940  ...                                      Billie Eilish
23    0.5990  ...                                      Billie Eilish
24    0.1880  ...                                      Billie Eilish
25    0.3630  ...                                      Billie Eilish
26    0.1230  ...                                      Billie Eilish
27    0.3790  ...                      Billie Eilish & Vince Staples
28    0.3180  ...                                      Billie Eilish
29    0.5730  ...                                      Billie Eilish
30    0.3070  ...                                      Billie Eilish
31    0.7250  ...                                 The Rolling Stones
32    0.8250  ...                                 The Rolling Stones
33    0.3740  ...                                 The Rolling Stones
34    0.6840  ...                                 The Rolling Stones
35    0.6820  ...                                 The Rolling Stones
36    0.7190  ...                                 The Rolling Stones
37    0.5650  ...                                 The Rolling Stones
38    0.9320  ...                                 The Rolling Stones
39    0.7060  ...                                 The Rolling Stones
40    0.7740  ...                                 The Rolling Stones
41    0.5460  ...                                 The Rolling Stones
42    0.9340  ...                                 The Rolling Stones
43    0.3120  ...                                            FINNEAS
44    0.8090  ...                                 The Rolling Stones
45    0.6420  ...                                 The Rolling Stones
46    0.3020  ...                                 The Rolling Stones
47    0.5370  ...                                 The Rolling Stones
48    0.3960  ...                                 The Rolling Stones
49    0.8000  ...                                 The Rolling Stones
50    0.5610  ...                                 The Rolling Stones
51    0.4990  ...                                 The Rolling Stones
52    0.5650  ...                                 The Rolling Stones
53    0.9000  ...                                 The Rolling Stones
54    0.2090  ...                                            FINNEAS
55    0.4520  ...                                            FINNEAS
56    0.2750  ...                                            FINNEAS
57  

* Вчитување на податоците за песните од playlist-тата кои се означени како како „лоши песни“.

In [ ]:
getData(username, bad_playlist)

Getting user playlist
Name: b'GOOD', Number of songs: 1004, Playlist ID: 0MSvVCtdco07nI3ZWQsl9Y 
Name: b'BAD', Number of songs: 987, Playlist ID: 4TMShuRj0r3ePfupxOa058 
Name: b'Test', Number of songs: 2939, Playlist ID: 7kxFRqwR0wEkkaXffQc5Gw 
Getting playlist content
Getting playlist audio features


In [ ]:
df_bad_spotipy = pd.read_csv("7m07drxdmjlwhmdhd17heiwb2-4TMShuRj0r3ePfupxOa058.csv")

In [ ]:
df_bad_spotipy.head(3000)

energy  ...                                             artist
0     0.859  ...                           Justin Bieber & Ludacris
1     0.833  ...                                      Justin Bieber
2     0.698  ...                                      Justin Bieber
3     0.590  ...                                      Justin Bieber
4     0.650  ...                                      Justin Bieber
5     0.811  ...                                      Justin Bieber
6     0.788  ...                    Justin Bieber & Jessica Jarrell
7     0.607  ...                      Sean Kingston & Justin Bieber
8     0.717  ...                                      Justin Bieber
9     0.603  ...                                      Justin Bieber
10    0.853  ...                                      Justin Bieber
11    0.681  ...                                      Justin Bieber
12    0.718  ...                                      Justin Bieber
13    0.733  ...                                      Justin Bieber
14    0.750  ...                                      Justin Bieber
15    0.520  ...                              Justin Bieber & Usher
16    0.794  ...                                               Ceca
17    0.669  ...                                               Ceca
18    0.794  ...                                               Ceca
19    0.698  ...                                               Ceca
20    0.828  ...                                               Ceca
21    0.819  ...                                               Ceca
22    0.836  ...                                               Ceca
23    0.911  ...                                               Ceca
24    0.665  ...                                               Ceca
25    0.870  ...                                               Ceca
26    0.614  ...                                               Ceca
27    0.816  ...                           Justin Bieber & Ludacris
28    0.550  ...                                      Justin Bieber
29    0.873  ...                           Justin Bieber & Big Sean
30    0.542  ...                                      Justin Bieber
31    0.706  ...                                      Justin Bieber
32    0.570  ...                              Justin Bieber & Drake
33    0.878  ...                                      Justin Bieber
34    0.705  ...                                      Justin Bieber
35    0.843  ...                        Justin Bieber & Nicki Minaj
36    0.612  ...                                      Justin Bieber
37    0.356  ...                                      Justin Bieber
38    0.438  ...                                      Justin Bieber
39    0.443  ...                                      Justin Bieber
40    0.681  ...                                      Justin Bieber
41    0.546  ...                              Justin Bieber & Quavo
42    0.506  ...                                      Justin Bieber
43    0.608  ...                                      Justin Bieber
44    0.483  ...               Justin Bieber & Post Malone & Clever
45    0.603  ...                          Justin Bieber & Lil Dicky
46    0.616  ...                                      Justin Bieber
47    0.777  ...                       Justin Bieber & Travis Scott
48    0.508  ...                            Justin Bieber & Kehlani
49    0.494  ...                                      Justin Bieber
50    0.412  ...                                      Justin Bieber
51    0.315  ...                                      Justin Bieber
52    0.437  ...                                      Justin Bieber
53    0.304  ...                                      Justin Bieber
54    0.578  ...                      Justin Bieber & Summer Walker
55    0.454  ...                      Cardi B & Megan Thee Stallion
56    0.785  ...                                               Ceca
57    0.605  ...                                             

* Спојување на двете податочни множества, на „добри“ и „лоши“ песни во едно податочно множество.

In [ ]:
df_spotipy = df_good_spotipy.append(df_bad_spotipy, ignore_index=True)

In [ ]:
df_spotipy.head(3000)

* Спојување на податоците собрани од двата извори во едно финално податочно множество, со join на табелите по името на песната(возможно бидејќи имињата на песните се уникатни - не постојат две песни со исто име во ова податочно множество).

In [ ]:
df_result.title.unique


<bound method Series.unique of 0                                                 bad guy
1                                                   xanny
2                            you should see me in a crown
3                           all the good girls go to hell
4                                       wish you were gay
5                                   when the party's over
6                                                       8
7                                    my strange addiction
8                                           bury a friend
9                                                 ilomilo
10                                     listen before i go
11                                             i love you
12                                                goodbye
13                                              my future
14                                         No Time To Die
15                                    everything i wanted
16      WHEN I WAS OLDER - Music Inspired

In [ ]:
df_result = pd.merge(df_spotipy, df_genres, on='title')

In [ ]:
df_result.head(5000)

energy  liveness    tempo  ...                  top genre  year  target
0     0.4250    0.1000  135.128  ...                 electropop  2019       1
1     0.1250    0.2650  111.554  ...                 electropop  2019       1
2     0.5330    0.1390  150.455  ...                 electropop  2019       1
3     0.4440    0.1770  185.044  ...                 electropop  2019       1
4     0.3510    0.7520  118.028  ...                 electropop  2019       1
5     0.1110    0.0897   82.642  ...                 electropop  2019       1
6     0.2350    0.1070   62.446  ...                 electropop  2019       1
7     0.3050    0.1050  100.029  ...                 electropop  2019       1
8     0.3890    0.1060  120.046  ...                 electropop  2019       1
9     0.4230    0.0896  120.020  ...                 electropop  2019       1
10    0.0561    0.3880   79.764  ...                 electropop  2019       1
11    0.1310    0.1090  137.446  ...                 electropop  2019       1
12    0.1380    0.2540   74.318  ...                 electropop  2019       1
13    0.3090    0.3520  104.745  ...                 electropop  2020       1
14    0.2190    0.0827   73.537  ...                 electropop  2020       1
15    0.2250    0.1060  120.006  ...                 electropop  2019       1
16    0.3320    0.0848  150.130  ...                 electropop  2019       1
17    0.3210    0.1140  145.045  ...                 electropop  2018       1
18    0.2960    0.0950  115.284  ...                 electropop  2018       1
19    0.4220    0.0958  120.033  ...                 electropop  2018       1
20    0.3880    0.3410  124.909  ...                 electropop  2017       1
21    0.4120    0.1160  170.163  ...                 electropop  2017       1
22    0.3940    0.1170   89.936  ...                 electropop  2017       1
23    0.5990    0.1030  165.212  ...                 electropop  2017       1
24    0.1880    0.1030  130.022  ...                 electropop  2017       1
25    0.3630    0.0840  144.892  ...                 electropop  2017       1
26    0.1230    0.0732  129.565  ...                 electropop  2017       1
27    0.3790    0.0969   82.531  ...                 electropop  2017       1
28    0.3180    0.0795  119.959  ...                 electropop  2017       1
29    0.5730    0.4820   99.939  ...                 electropop  2017       1
30    0.3070    0.0792   67.513  ...                 electropop  2016       1
31    0.7250    0.0889   85.270  ...                 album rock  1964       1
32    0.8250    0.3540  126.817  ...                 album rock  1964       1
33    0.3740    0.2080   87.593  ...                 album rock  1964       1
34    0.6840    0.0981   99.014  ...                 album rock  1964       1
35    0.6820    0.2560   97.849  ...                 album rock  1964       1
36    0.7190    0.1550   87.743  ...                 album rock  1964       1
37    0.5650    0.0565  105.423  ...                 album rock  1964       1
38    0.9320    0.3240  177.340  ...                 album rock  1964       1
39    0.7060    0.5160  122.015  ...                 album rock  1964       1
40    0.7740    0.0669   97.035  ...                 album rock  1964       1
41    0.5460    0.1660  102.634  ...                 album rock  1964       1
42    0.9340    0.0965  125.275  ...                 album rock  1964       1
43    0.3120    0.1220  144.987  ...                 electropop  2020       1
44    0.8090    0.0561  105.625  ...                 album rock  1973       1
45    0.6420    0.5300  105.139  ...                 album rock  1973       1
46    0.3020    0.1030   73.047  ...                 album rock  1973       1
47    0.5370    0.1330  111.085  ...                 album rock  1973       1
48    0.3960    0.1430  138.241  ...                 album rock  1973       1
49    0.8000    0.6700  147.171  ...                 album rock  1973       1
50    0.5610    0.2160  109.

* Зачувување на податочното множество во посебен csv file.

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
cd drive/My\ Drive/Colab\ Notebooks

/content/drive/My Drive/Colab Notebooks


In [ ]:
df_result.to_csv("16v9v2020.csv")